# Processo de ETL para Dados de Licitações e Contratos do TCU - Camada Business

Esta seção descreve o processo ETL para a camada `business` do arquivo "Informativo de Licitações e Contratos" do Tribunal de Contas da União (TCU). Após passar pelas camadas `raw` e `trusted`, os dados chegam à camada `business`, onde são organizados e tratados para análises e consumo final.

## Visão Geral do ETL

O processo de ETL para a camada `business` envolve etapas adicionais de transformação para normalizar e padronizar os dados de acórdãos do TCU. Estas operações ajudam a garantir a consistência das informações e adequação ao formato desejado para análise e visualização.

### Estrutura dos DataFrames

1. **DataFrame da Camada Trusted**: 
   - Colunas: `informativo_acordao`, `titulo_acordao`, `colegiado_acordao`, `texto_acordao`, `enunciado_acordao`, `numero_acordao`, `infos_acordao`, `tag_acordao`, `tipo_acordao`, `relator_acordao`, `ano_acordao`

2. **DataFrame Final na Camada Business**:
   - Colunas: `titulo_acordao`, `colegiado_acordao`, `enunciado_acordao`, `numero_acordao`, `infos_acordao`, `tipo_acordao`, `relator_acordao`, `ano_acordao`, `tipo_relator_acordao`

### Principais Transformações

1. **Seleção de Colunas**:
   - As colunas relevantes são selecionadas a partir da camada `trusted`, descartando campos desnecessários. 

2. **Normalização do Campo `relator_acordao`**:
   - Uma nova coluna, `tipo_relator_acordao`, é criada para classificar o tipo de relator (`Ministro`, `Ministro-Substituto` ou `Desconhecido`), baseado em palavras-chave no campo `relator_acordao`.
   - Remoção das expressões "Relator Ministro" ou "Relator Ministro-Substituto" do campo `relator_acordao` para manter apenas o nome.

3. **Limpeza de Espaços em Branco**:
   - Espaços extras são removidos do campo `relator_acordao`.

## Estrutura Final do DataFrame

| Campo               | Descrição                                                                                         |
|---------------------|---------------------------------------------------------------------------------------------------|
| `titulo_acordao`    | Título do acórdão.                                                                                |
| `colegiado_acordao` | Colegiado responsável pelo julgamento.                                                            |
| `enunciado_acordao` | Resumo do entendimento contido na deliberação.                                                    |
| `numero_acordao`    | Número de publicação do acórdão.                                                                  |
| `infos_acordao`     | Descrição detalhada do acórdão.                                                                   |
| `tipo_acordao`      | Tipo do acórdão (e.g., licitação, contrato).                                                      |
| `relator_acordao`   | Nome do relator responsável, com formatação limpa.                                                |
| `ano_acordao`       | Ano de publicação do acórdão.                                                                     |
| `tipo_relator_acordao` | Classificação do tipo de relator (`Ministro`, `Ministro-Substituto` ou `Desconhecido`).       |

## Tecnologias Utilizadas

- **AWS S3**: Armazena os dados em diferentes camadas.
- **PySpark/Databricks**: Processa e organiza os dados para a camada `business`.

## Exemplo de Uso dos Dados

Os dados processados podem ser usados para:
- Análises detalhadas de acórdãos de licitações e contratos.
- Geração de relatórios e insights sobre deliberações do TCU.
- Visualização de dados interativa para conformidade em processos licitatórios.

In [0]:
from pyspark.sql.functions import udf, regexp_extract, split, regexp_replace, when, trim
from pyspark.sql.types import IntegerType, StringType
from pyspark.sql.utils import AnalysisException
from py4j.protocol import Py4JJavaError
from datetime import datetime
import urllib
import os

In [0]:
dt_load = datetime.today().strftime('%Y%m%d')

In [0]:
ACCESS_KEY = os.getenv("AWS_SECRET_ACCESS_KEY")
SECRET_KEY = os.getenv("AWS_ACCESS_KEY_ID")
ENCODED_SECRET_KEY = urllib.parse.quote(string=SECRET_KEY, safe="")
AWS_S3_BUCKET = os.getenv("S3_BUCKET_NAME")


In [0]:
layer = "trusted"
final_layer = "business"
area = "tcu"
context = "boletim-informativo-lc"
file_name = "boletim-informativo-lc"
file_format = "parquet"
write_mode = "overwrite"

In [0]:
MOUNT_NAME = f"/mnt/{AWS_S3_BUCKET}"
SOURCE_URL = f"s3n://{ACCESS_KEY}:{ENCODED_SECRET_KEY}@{AWS_S3_BUCKET}"

if not any(mount.mountPoint == f"/mnt/{AWS_S3_BUCKET}" for mount in dbutils.fs.mounts()):
    dbutils.fs.mount(SOURCE_URL, MOUNT_NAME)
else:
    print("Diretório já montado.")


Diretório já montado.


In [0]:
display(dbutils.fs.ls(f"/mnt/{AWS_S3_BUCKET}/{layer}/{area}/{context}/{dt_load}/{file_name}"))

path name size modificationTime dbfs:/mnt/thereal-slim-shady/trusted/tcu/boletim-informativo-lc/20241109/boletim-informativo-lc/_SUCCESS _SUCCESS 0 1731176162000 dbfs:/mnt/thereal-slim-shady/trusted/tcu/boletim-informativo-lc/20241109/boletim-informativo-lc/_committed_6635152626149563876 _committed_6635152626149563876 222 1731176162000 dbfs:/mnt/thereal-slim-shady/trusted/tcu/boletim-informativo-lc/20241109/boletim-informativo-lc/_started_6635152626149563876 _started_6635152626149563876 0 1731176159000 dbfs:/mnt/thereal-slim-shady/trusted/tcu/boletim-informativo-lc/20241109/boletim-informativo-lc/part-00000-tid-6635152626149563876-a0697967-fb90-4ed5-9444-36071a3068ae-26-1-c000.snappy.parquet part-00000-tid-6635152626149563876-a0697967-fb90-4ed5-9444-36071a3068ae-26-1-c000.snappy.parquet 2096557 1731176161000 dbfs:/mnt/thereal-slim-shady/trusted/tcu/boletim-informativo-lc/20241109/boletim-informativo-lc/part-00001-tid-6635152626149563876-a0697967-fb90-4ed5-9444-36071a3068ae-27-1-c000.snappy.parquet part-00001-tid-6635152626149563876-a0697967-fb90-4ed5-9444-36071a3068ae-27-1-c000.snappy.parquet 1278010 1731176160000

In [0]:
file_type = "parquet"
infer_schema = "true"
file_location = f"/mnt/{AWS_S3_BUCKET}/{layer}/{area}/{context}/{dt_load}/{file_name}"
df_trusted = spark.read.format(file_type).option("inferSchema", infer_schema).load(file_location) 

In [0]:
df_trusted.columns

Out[39]: ['informativo_acordao',
 'titulo_acordao',
 'colegiado_acordao',
 'texto_acordao',
 'enunciado_acordao',
 'numero_acordao',
 'infos_acordao',
 'tag_acordao',
 'tipo_acordao',
 'relator_acordao',
 'ano_acordao']

In [0]:
df_selected = df_trusted[['titulo_acordao','colegiado_acordao','enunciado_acordao','numero_acordao','infos_acordao','tipo_acordao','relator_acordao','ano_acordao']]

In [0]:
df_treated = (
    df_selected
    .withColumn("tipo_relator_acordao", 
                when(df_selected["relator_acordao"].contains("Relator Ministro"), "Ministro")
                .when(df_selected["relator_acordao"].contains("Relator Ministro-Substituto"), "Ministro-Substituto")
                .otherwise("Desconhecido"))
    .withColumn("relator_acordao", regexp_replace('relator_acordao', 'Relator Ministro(-Substituto)?', ''))
)

titulo_acordao colegiado_acordao enunciado_acordao numero_acordao infos_acordao tipo_acordao relator_acordao ano_acordao tipo_relator_acordao Informativo de Licitações e Contratos 478/2024 Plenário O critério definido no art. 59, § 4º, da Lei 14.133/2021 conduz a uma presunção relativa de inexequibilidade de preços, devendo a Administração, nos termos do art. 59, § 2º, da referida lei, dar à licitante a oportunidade de demonstrar a exequibilidade de sua proposta. 478 "Representação formulada ao TCU apontou possíveis irregularidades na Concorrência 1/2023, do tipo menor preço e com modo de disputa aberto, realizada pela Universidade Federal Rural de Pernambuco (UFRPE), sob a regência da Lei 14.133/2021 e tendo por objeto a ""contratação de serviços especiais de engenharia relacionados à realização de planejamento, levantamentos, ensaios e a elaboração dos projetos executivos de engenharia, arquitetura e documentações legais referentes à construção do Campus definitivo da Unidade Acadêmica de Belo Jardim (UABJ)"". A sessão pública de recebimento e abertura de propostas, bem como de disputa de lances, contara com a participação de 31 empresas, sendo que as dezoito primeiras colocadas tiveram suas propostas desclassificadas por suposta inexequibilidade, em razão de haverem ofertado valor inferior a 75% do orçamento-base da licitação. Em face disso, a representante alegou, em essência, que: i) ""sua desclassificação teria sido feita de maneira sumária, sem que tenham sido promovidas as diligências necessárias previstas no art. 59, § 2º, da Lei 14.133/2021 e no próprio edital de licitação (subitem 6.10) para fins de demonstração da exequibilidade das melhores propostas apresentadas pelos licitantes""; ii) o valor proposto pela empresa vencedora teria sido 77% superior ao da proposta mais vantajosa, ""a qual teria sido desclassificada de maneira sumária, sem que tenha sido feita qualquer diligência""; iii) ""o entendimento jurisprudencial dominante pelo Poder Judiciário e pelo TCU seria no sentido de que é relativa e não absoluta a presunção de inexequibilidade das propostas inferiores a 75% do valor orçado pela Administração, cabendo, conforme o art. 59, § 2º, da Lei 14.133/2021, facultar às licitantes a demonstração da exequibilidade de suas propostas"". A partir do exame dos documentos e das informações relativas à Concorrência 1/2023, a unidade técnica entendeu que, de fato, as desclassificações das propostas apresentadas pelas licitantes ocorreram de forma sumária, sem que fosse dada oportunidade para que as empresas se manifestassem sobre a sua exequibilidade, o que, em tese, não seria procedimento condizente com o art. 59, § 2º, da Lei 14.133/2021, segundo o qual ""a Administração poderá realizar diligências para aferir a exequibilidade das propostas ou exigir das licitantes sua demonstração"". A unidade instrutiva também afirmou que a ausência de oportunidade para as licitantes demonstrarem a exequibilidade de suas propostas seria procedimento contrário à jurisprudência do Tribunal, ""conforme a Súmula TCU 262 e Acórdãos 1244/2018-TCU-Plenário; 2528/2012-TCU-Plenário; 1079/2017-TCU-Plenário; e 1161/2014-TCU-Plenário"". Realizada a oitiva prévia da UFRPE, esta informou haver retornado o certame à fase de julgamento das propostas e realizado diligências, junto às empresas que apresentaram propostas com valores inferiores a 75% do orçamento estimativo da licitação, para demonstração de sua exequibilidade, em cumprimento ao disposto no art. 59, § 2º, da Lei 14.133/2021. Dessa forma, a unidade técnica concluiu que a representação perdera seu objeto, propondo então que ela fosse considerada prejudicada, com o consequente arquivamento dos autos. Em seu voto, não obstante anuir à conclusão de que a representação ""perdeu seu objeto, ante o saneamento da irregularidade"", o relator julgou pertinente aduzir comentários acerca do art. 59 da Lei 14.133/2021, que assim dispõe: ""Art. 59. Serão desclassificadas as propostas que: [...] IV -

In [0]:
df_trimed = df_treated.withColumn("relator_acordao", trim(df_treated["relator_acordao"]))

In [0]:
df = df_trimed.fillna({'tipo_relator_acordao': 'Desconhecido'})

display(df.head(5))

titulo_acordao colegiado_acordao enunciado_acordao numero_acordao infos_acordao tipo_acordao relator_acordao ano_acordao tipo_relator_acordao Informativo de Licitações e Contratos 478/2024 Plenário O critério definido no art. 59, § 4º, da Lei 14.133/2021 conduz a uma presunção relativa de inexequibilidade de preços, devendo a Administração, nos termos do art. 59, § 2º, da referida lei, dar à licitante a oportunidade de demonstrar a exequibilidade de sua proposta. 478 "Representação formulada ao TCU apontou possíveis irregularidades na Concorrência 1/2023, do tipo menor preço e com modo de disputa aberto, realizada pela Universidade Federal Rural de Pernambuco (UFRPE), sob a regência da Lei 14.133/2021 e tendo por objeto a ""contratação de serviços especiais de engenharia relacionados à realização de planejamento, levantamentos, ensaios e a elaboração dos projetos executivos de engenharia, arquitetura e documentações legais referentes à construção do Campus definitivo da Unidade Acadêmica de Belo Jardim (UABJ)"". A sessão pública de recebimento e abertura de propostas, bem como de disputa de lances, contara com a participação de 31 empresas, sendo que as dezoito primeiras colocadas tiveram suas propostas desclassificadas por suposta inexequibilidade, em razão de haverem ofertado valor inferior a 75% do orçamento-base da licitação. Em face disso, a representante alegou, em essência, que: i) ""sua desclassificação teria sido feita de maneira sumária, sem que tenham sido promovidas as diligências necessárias previstas no art. 59, § 2º, da Lei 14.133/2021 e no próprio edital de licitação (subitem 6.10) para fins de demonstração da exequibilidade das melhores propostas apresentadas pelos licitantes""; ii) o valor proposto pela empresa vencedora teria sido 77% superior ao da proposta mais vantajosa, ""a qual teria sido desclassificada de maneira sumária, sem que tenha sido feita qualquer diligência""; iii) ""o entendimento jurisprudencial dominante pelo Poder Judiciário e pelo TCU seria no sentido de que é relativa e não absoluta a presunção de inexequibilidade das propostas inferiores a 75% do valor orçado pela Administração, cabendo, conforme o art. 59, § 2º, da Lei 14.133/2021, facultar às licitantes a demonstração da exequibilidade de suas propostas"". A partir do exame dos documentos e das informações relativas à Concorrência 1/2023, a unidade técnica entendeu que, de fato, as desclassificações das propostas apresentadas pelas licitantes ocorreram de forma sumária, sem que fosse dada oportunidade para que as empresas se manifestassem sobre a sua exequibilidade, o que, em tese, não seria procedimento condizente com o art. 59, § 2º, da Lei 14.133/2021, segundo o qual ""a Administração poderá realizar diligências para aferir a exequibilidade das propostas ou exigir das licitantes sua demonstração"". A unidade instrutiva também afirmou que a ausência de oportunidade para as licitantes demonstrarem a exequibilidade de suas propostas seria procedimento contrário à jurisprudência do Tribunal, ""conforme a Súmula TCU 262 e Acórdãos 1244/2018-TCU-Plenário; 2528/2012-TCU-Plenário; 1079/2017-TCU-Plenário; e 1161/2014-TCU-Plenário"". Realizada a oitiva prévia da UFRPE, esta informou haver retornado o certame à fase de julgamento das propostas e realizado diligências, junto às empresas que apresentaram propostas com valores inferiores a 75% do orçamento estimativo da licitação, para demonstração de sua exequibilidade, em cumprimento ao disposto no art. 59, § 2º, da Lei 14.133/2021. Dessa forma, a unidade técnica concluiu que a representação perdera seu objeto, propondo então que ela fosse considerada prejudicada, com o consequente arquivamento dos autos. Em seu voto, não obstante anuir à conclusão de que a representação ""perdeu seu objeto, ante o saneamento da irregularidade"", o relator julgou pertinente aduzir comentários acerca do art. 59 da Lei 14.133/2021, que assim dispõe: ""Art. 59. Serão desclassificadas as propostas que: [...] IV -

In [0]:
df.write.save(f"/mnt/{AWS_S3_BUCKET}/{final_layer}/{area}/{context}/{dt_load}/{file_name}", format=file_format,mode=write_mode)